In [38]:
pip install newspaper3k

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.1/211.1 kB 7.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.1/81.1 kB 3.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 13.8 MB/s eta 0:00:0000:0100:01
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
  Created wheel for tinysegmenter: filename=tinysegmenter-0.3-py3-none-any.whl size=13540 sha256=ac2816e7ed5ca93705a1016f06e044f2425db2e0497217a91002ba54bccb3145
  Stored in directory: /Users/akin/Library/Caches/pip/wheels/9e/14/bb/6f49188191db1acb539a457f2870a07a85f077526b9ad458cd
  Created wheel for feedfinder2: filename=feedfinder2-0.0.4-py3-none-any.whl size=3339 sha256=ca65029ef227eaffe2c15271cd51975ba5108caa609d8c9e725b67765832fed8
  Stored in directory: /Users/akin/Library/Caches/pip/wheels/15/21/7d/18b75fa5ae96421e6b78578f5299a350c6794cd16119173b63
  Created wheel for jie

## Importing Libraries

In [1]:
import pandas as pd
import numpy as np
import requests
from bs4 import BeautifulSoup
import csv
import re
import time
from newspaper import Article

## Get Ticker tape Nifty 200 URLs

In [2]:
#Header Agent
header_agent = {'User-Agent': 'Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.11 (KHTML, like Gecko) Chrome/23.0.1271.64 Safari/537.11',
       'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8',
       'Accept-Charset': 'ISO-8859-1,utf-8;q=0.7,*;q=0.3',
       'Accept-Encoding': 'none',
       'Accept-Language': 'en-US,en;q=0.8',
       'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8',
       'Connection': 'keep-alive'}

#Ticekr tape Nift 200 page url
url = "https://www.tickertape.in/indices/nifty-500-index-.NIFTY500/constituents"

#Requesting webpage data from the server that hosts the website. Server responds to this is by sending data.
tickerpage = requests.get(url,headers=header_agent)

In [3]:
#Now we will check if the requested data from URL is loaded successfully or not

if tickerpage.status_code == 200:
    print("Success : Requested ticker tape page is loaded successfully ")
else:
    print("Failure : We have encountered an error while loading the page")

Success : Requested ticker tape page is loaded successfully 


In [4]:
#Load the content from the page
ticker_content = tickerpage.content

In [5]:
#Now using HTMLParser we will be parsing from ticker_content and format in into HTML
ticker_soup = BeautifulSoup(ticker_content,'html.parser')
#Now to view the html doc which is being extracted in a more readable format we will use prettify()
ticker_soup.prettify()

'<!DOCTYPE html>\n<html lang="en-US">\n <head>\n  <meta charset="utf-8" class="jsx-2462095555"/>\n  <meta class="jsx-2462095555" content="width=device-width, initial-scale=1, maximum-scale=1, user-scalable=no, viewport-fit=cover" name="viewport"/>\n  <title>\n   Nifty 500 Index: Constituent stocks\n  </title>\n  <meta content="Get detailed constituents\' stocks pattern of Nifty 500 Index Index - Analyze stocks\' price, contribution percentage, index share and marketcap" name="description"/>\n  <meta content="Exchange-traded funds, NIFTY 500 NAV price, latest market price, Nifty 500 Index Constituents, Nifty 500 Index, Nifty 500, Index, fundamental analysis, Finance, India" name="keywords"/>\n  <meta content="Nifty 500 Index: Constituent stocks" property="og:title"/>\n  <meta content="website" property="og:type"/>\n  <meta content="https://www.tickertape.in/indices/nifty-500-index-.NIFTY500/constituents" property="og:url"/>\n  <meta content="https://assets.tickertape.in/og/indices/.NIFT

In [6]:
#Extracting from that section of the webpage where all products which we are trying to scrape are
block = ticker_soup.find('div', attrs = {'class':'jsx-3678921272 constituent-list-wrapper'})
print(block)

<div class="jsx-3678921272 constituent-list-wrapper"><div class="jsx-4205508398 text-secondary relative constituent-data-row-holder"><div class="jsx-4205508398 constituent-data-row row relative d-flex"><div class="jsx-4205508398 text-14 col-1 d-flex-col"><h5 class="jsx-4205508398 w-full ellipsis mb2"><a class="jsx-4205508398 typography-body-medium-m text-primary desktop--only constituent-name" href="/stocks/aditya-birla-fashion-and-retail-ADIA" rel="noreferrer noopener" target="_blank" title="Aditya Birla Fashion and Retail Ltd | ABFRL | Consumer Discretionary">Aditya Birla Fashion and Retail Ltd</a></h5><div class="jsx-4205508398 d-flex-col"><div class="jsx-4205508398 d-flex"><span class="jsx-4205508398 typography-caption-medium ticker text-uppercase mr4">ABFRL</span><div class="jsx-4205508398 mob--only d-flex text-12"><span class="jsx-4205508398 typography-body-regular-xs change percentage-value up"><i class="jsx-4205508398 icon-Green-up"></i><span class="jsx-4205508398">0.53%</span>

In [7]:
company_url=[]
for company in block:
    #product_url
    url = "https://www.tickertape.in"+company.find('a')['href']
    company_url.append(url)
    print(url)
print("Number URLs for which we are extracting Data are :",len(company_url))

https://www.tickertape.in/stocks/aditya-birla-fashion-and-retail-ADIA
https://www.tickertape.in/stocks/affle-india-AFFL
https://www.tickertape.in/stocks/aarti-drugs-ADRG
https://www.tickertape.in/stocks/aarti-industries-ARTI
https://www.tickertape.in/stocks/acc-ACC
https://www.tickertape.in/stocks/adani-green-energy-ADNA
https://www.tickertape.in/stocks/adani-transmission-ADAI
https://www.tickertape.in/stocks/aditya-birla-capital-ADTB
https://www.tickertape.in/stocks/adani-ports-and-special-economic-zone-APSE
https://www.tickertape.in/stocks/abb-india-ABB
https://www.tickertape.in/stocks/aegis-logistics-AEGS
https://www.tickertape.in/stocks/adani-power-ADAN
https://www.tickertape.in/stocks/adani-enterprises-ADEL
https://www.tickertape.in/stocks/3m-india-TMIN
https://www.tickertape.in/stocks/abbott-india-ABOT
https://www.tickertape.in/stocks/aia-engineering-AIAE
https://www.tickertape.in/stocks/adani-gas-ADAG
https://www.tickertape.in/stocks/aavas-financiers-AVAS
https://www.tickertape.

# Create company list file with all details From Ticker tape

In [9]:
#Now we will extract all the information which we require and we will put all the information extracted in an tsv format file
header_agent = {'User-Agent': 'Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.11 (KHTML, like Gecko) Chrome/23.0.1271.64 Safari/537.11',
       'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8',
       'Accept-Charset': 'ISO-8859-1,utf-8;q=0.7,*;q=0.3',
       'Accept-Encoding': 'none',
       'Accept-Language': 'en-US,en;q=0.8',
       'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8',
       'Connection': 'keep-alive'}
with open('companyList.tsv','w',newline='',encoding="utf-8") as file:
    headers = ['sNo','Company Name','Full Company Name','sc Performance','sc Valuation','sc Growth','sc Profitability','sc Entry Point','sc Red Flags','Income Statements','2019 Total Revenue','2019 EBITDA','2019 Net Income','2019 PBT','2020 Total Revenue','2020 EBITDA','2020 Net Income','2020 PBT','2021 Total Revenue','2021 EBITDA','2021 Net Income','2021 PBT','2022 Total Revenue','2022 EBITDA','2022 Net Income','2022 PBT','PE Ratio']

    writer = csv.writer(file,delimiter='\t')
    writer.writerow(headers)
    SNo = 0
    for url_val in company_url:
        url_val_finance=url_val + "/financials?checklist=basic&statement=income&view=normal&period=annual"
        url_val_overview=url_val + "?checklist=basic&chartScope=1d"
        SNo=SNo+1
        print(SNo)
        
        company_ovr_page = requests.get(url_val_overview,headers=header_agent,stream=True)
        print(url_val_overview)
        if company_ovr_page.status_code == 200:
            print("Success : Requested ticker tape page is loaded successfully ")
            
            company_ovr_content = company_ovr_page.content
            comp_ovr_soup = BeautifulSoup(company_ovr_content,"html.parser")
#             print(comp_ovr_soup.text)
            part_1 = comp_ovr_soup.find('div', attrs ={'class':'jsx-3488654145 sidebar desktop--only stock-security-sidebar'})
#             print(part_1.text)
            CompanyName = part_1.find('span', attrs ={'class':'jsx-3488654145 ticker text-teritiary font-medium'}).get_text()
            FullCompanyName = part_1.find('div', attrs ={'class':'jsx-3488654145 full-width d-flex justify-space-between sidebar-security-name'}).get_text()
            print(CompanyName)
            print(FullCompanyName)
            
            key_metrics = comp_ovr_soup.find('div', attrs ={'class':'jsx-3519906982 stat-table-wrapper'})
            count=0
            for row in key_metrics.thead.find_all('tr'):    
                columns = row.find_all('th')
                
                for column in columns:
                    if(column.text == "No LabelNo Label"):
                        i=count
                    count=count+1
            for row in key_metrics.tbody.find_all('tr'):    
                columns = row.find_all('td')
                PERatio=columns[i].text
                print(PERatio)
            
            
            try:
                scorecard = comp_ovr_soup.find('div', attrs ={'class':'jsx-1630544676 scorecard-container relative'})
#                     print(scorecard)
                string = scorecard.get_text()
                soup = True
            except:
                soup = False
        company_fin_page = requests.get(url_val_finance,headers=header_agent,stream=True)
        print(url_val_finance)
        if company_fin_page.status_code == 200 :
            print("Success : Requested ticker tape page is loaded successfully ")
#             print(comp_ovr_soup.text)
            
            company_fin_content = company_fin_page.content
            comp_fin_soup = BeautifulSoup(company_fin_content,"html.parser")
#             print(comp_fin_soup.text)
            if soup == False:
                try:
                    scorecard = comp_fin_soup.find('div', attrs ={'class':'jsx-1630544676 scorecard-container relative'})
    #                     print(scorecard)
                    string = scorecard.get_text()
                    soup = True
                except:
                    soup = False
            if soup == True:
                string = string.replace("Scorecard","" , 1)
                string = string.replace("Performance","\nPerformance ")
                string = string.replace("Valuation","\nValuation ")
                string = string.replace("Growth","\nGrowth ")
                string = string.replace("Profitability","\nProfitability ")
                string = string.replace("Entry point","\nEntry point ")
                string = string.replace("Red flags","\nRed flags ")
                string = string.replace("Avg"," Avg ")
                string = string.replace("High"," High ")
                string = string.replace("Low"," Low ")
                string = string.replace("Good"," Good ")
                sc_array = re.split('\n',string)
                for i in sc_array:
                    split_sc_array = i.split(" ",1)
                    if(split_sc_array[0] == "Performance" ):
                        sc_Performance=split_sc_array[1]
                    elif(split_sc_array[0] == "Valuation" ):
                        sc_Valuation=split_sc_array[1]
                    elif(split_sc_array[0] == "Growth" ):
                        sc_Growth=split_sc_array[1]
                    elif(split_sc_array[0] == "Profitability" ):
                        sc_Profitability=split_sc_array[1]
                    elif(split_sc_array[0] == "Entry" ):
                        sc_Entrypoint=split_sc_array[1].split(" ",1)
                        sc_Entrypoint = sc_Entrypoint[1]
                    elif(split_sc_array[0] == "Red" ):
                        sc_Redflags=split_sc_array[1].split(" ",1)
                        sc_Redflags=sc_Redflags[1]
                print(sc_Performance)
                print(sc_Valuation)
                print(sc_Growth)
                print(sc_Profitability)
                print(sc_Entrypoint)
                print(sc_Redflags)
            

            
            
            try:
                IncomeStatement= comp_fin_soup.find('div',attrs ={'class':'jsx-2537935686 commentary-items'}).text
            except:
                IncomeStatement= "Income statement not found"
            print(IncomeStatement)
            table = comp_fin_soup.find('table',class_='jsx-2597786574 jsx-1728146729')
            count=0
            i2019=i2020=i2021=i2022=-1
            try:
                for row in table.thead.find_all('tr'):    
                    columns = row.find_all('th')
                    for column in columns:
                        if(column.text == "FY 2019"):
                            i2019=count
                        elif(column.text == "FY 2020"):
                            i2020=count
                        elif(column.text == "FY 2021"):
                            i2021=count
                        elif(column.text == "FY 2022"):
                            i2022=count
                        count=count+1
                
                for row in table.tbody.find_all('tr'):    
                    columns = row.find_all('td')
                    if(columns[0].text == "Total Revenue"):
                        if(i2019 != -1):
                            TotalRevenue2019=columns[i2019].text
                        else:
                            TotalRevenue2019="NAN" 
                        if(i2020 != -1):
                            TotalRevenue2020=columns[i2020].text
                        else:
                            TotalRevenue2020="NAN" 
                        if(i2021 != -1):
                            TotalRevenue2021=columns[i2021].text
                        else:
                            TotalRevenue2021="NAN" 
                        if(i2022 != -1):
                            TotalRevenue2022=columns[i2022].text
                        else:
                            TotalRevenue2022="NAN" 
                    elif(columns[0].text == "EBITDA"):
                        if(i2019 != -1):
                            EBITDA2019=columns[i2019].text
                        else:
                            EBITDA2019="NAN"
                        if(i2020 != -1):
                            EBITDA2020=columns[i2020].text
                        else:
                            EBITDA2020="NAN"
                        if(i2021 != -1):
                            EBITDA2021=columns[i2021].text
                        else:
                            EBITDA2021="NAN"
                        if(i2022 != -1):
                            EBITDA2022=columns[i2022].text
                        else:
                            EBITDA2022="NAN"
                    elif(columns[0].text == "Net Income"):
                        if(i2019 != -1):
                            NetIncome2019=columns[i2019].text
                        else:
                            NetIncome2019="NAN"
                        if(i2020 != -1):
                            NetIncome2020=columns[i2020].text
                        else:
                            NetIncome2020="NAN"
                        if(i2021 != -1):
                            NetIncome2021=columns[i2021].text
                        else:
                            NetIncome2021="NAN"
                        if(i2022 != -1):
                            NetIncome2022=columns[i2022].text
                        else:
                            NetIncome2022="NAN"
                    elif(columns[0].text == "PBT"):
                        if(i2019 != -1):
                            PBT2019=columns[i2019].text
                        else:
                            PBT2019="NAN"
                        if(i2020 != -1):
                            PBT2020=columns[i2020].text
                        else:
                            PBT2020="NAN"
                        if(i2021 != -1):
                            PBT2021=columns[i2021].text
                        else:
                            PBT2021="NAN"
                        if(i2022 != -1):
                            PBT2022=columns[i2022].text
                        else:
                            PBT2022="NAN"
            except:
                TotalRevenue2019="NAN"
                TotalRevenue2020="NAN"
                TotalRevenue2021="NAN"
                TotalRevenue2022="NAN"
                EBITDA2019="NAN"
                EBITDA2020="NAN"
                EBITDA2021="NAN"
                EBITDA2022="NAN"
                NetIncome2019="NAN"
                NeIncome2020="NAN"
                NetIncome2021="NAN"
                NetIncome2022="NAN"
                PBT2019="NAN"
                PBT2020="NAN"
                PBT2021="NAN"
                PBT2022="NAN"
            row = [SNo,CompanyName,FullCompanyName,sc_Performance,sc_Valuation,sc_Growth,sc_Profitability,sc_Entrypoint,sc_Redflags,IncomeStatement,TotalRevenue2019,EBITDA2019,NetIncome2019,PBT2019,TotalRevenue2020,EBITDA2020,NetIncome2020,PBT2020,TotalRevenue2021,EBITDA2021,NetIncome2021,PBT2021,TotalRevenue2022,EBITDA2022,NetIncome2022,PBT2022,PERatio]
            writer.writerow(row)
            print(TotalRevenue2019)
            print(TotalRevenue2020)
            print(TotalRevenue2021)
            print(TotalRevenue2022)
            print(EBITDA2019)
            print(EBITDA2020)
            print(EBITDA2021)
            print(EBITDA2022)
            print(NetIncome2019)
            print(NetIncome2020)
            print(NetIncome2021)
            print(NetIncome2022)
            print(PBT2019)
            print(PBT2020)
            print(PBT2021)
            print(PBT2022)
            print("-------------------------------------------------")

1
https://www.tickertape.in/stocks/aditya-birla-fashion-and-retail-ADIA?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
ABFRL
Aditya Birla Fashion and Retail Ltd
-522.45
https://www.tickertape.in/stocks/aditya-birla-fashion-and-retail-ADIA/financials?checklist=basic&statement=income&view=normal&period=annual
Success : Requested ticker tape page is loaded successfully 
 Low Hasn't faired well - amongst the low performers
 High Seems to be overvalued vs the market average
 Low Lagging behind the market in financials growth
 High Showing good signs of profitability & efficiency
 Avg The stock is not in the overbought zone
 Low No red flag found
Higher than Industry Revenue GrowthA higher-than-industry revenue growth represents increased potential for the company to increase their market shareOver the last 5 years, revenue has grown at a yearly rate of 4.41%, vs industry avg of 4.31%Increasing Market ShareMarket share is the percentage of an indus

https://www.tickertape.in/stocks/adani-transmission-ADAI?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
ADANITRANS
Adani Transmission Ltd
73.76
https://www.tickertape.in/stocks/adani-transmission-ADAI/financials?checklist=basic&statement=income&view=normal&period=annual
Success : Requested ticker tape page is loaded successfully 
Higher than Industry Revenue GrowthA higher-than-industry revenue growth represents increased potential for the company to increase their market shareOver the last 5 years, revenue has grown at a yearly rate of 34.05%, vs industry avg of 3.79%Increasing Market ShareMarket share is the percentage of an industry's total sales going to a particular company. It gives a general idea of the size of a company v/s its competitorsOver the last 5 years, market share increased from 6.24% to 25.11%Higher than Industry Net IncomeNet income is equal to net earnings (profit) less expenses. This number is an important measure of how

https://www.tickertape.in/stocks/adani-enterprises-ADEL?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
ADANIENT
Adani Enterprises Ltd
123.63
https://www.tickertape.in/stocks/adani-enterprises-ADEL/financials?checklist=basic&statement=income&view=normal&period=annual
Success : Requested ticker tape page is loaded successfully 
 High The creamy layer - amongst the top performing stocks
 High Seems to be overvalued vs the market average
 Avg Financials growth has been moderate for a few years
 High Showing good signs of profitability & efficiency
 Avg The stock is overpriced but is not in the overbought zone
 Avg The stock has a moderate number of red flags
Higher than Industry Revenue GrowthA higher-than-industry revenue growth represents increased potential for the company to increase their market shareOver the last 5 years, revenue has grown at a yearly rate of 13.52%, vs industry avg of 10.25%Increasing Market ShareMarket share is the percen

https://www.tickertape.in/stocks/amara-raja-batteries-AMAR?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
AMARAJABAT
Amara Raja Batteries Ltd
15.38
https://www.tickertape.in/stocks/amara-raja-batteries-AMAR/financials?checklist=basic&statement=income&view=normal&period=annual
Success : Requested ticker tape page is loaded successfully 
 Low Hasn't faired well - amongst the low performers
 High Seems to be overvalued vs the market average
 Low Lagging behind the market in financials growth
 High Showing good signs of profitability & efficiency
 Good The stock is underpriced and is not in the overbought zone
 Low No red flag found
Higher than Industry Revenue GrowthA higher-than-industry revenue growth represents increased potential for the company to increase their market shareOver the last 5 years, revenue has grown at a yearly rate of 10.34%, vs industry avg of 7.32%Increasing Market ShareMarket share is the percentage of an industry's total

 Avg Price return has been average, nothing exciting
 High Seems to be overvalued vs the market average
 Low Lagging behind the market in financials growth
 High Showing good signs of profitability & efficiency
 Avg The stock is overpriced but is not in the overbought zone
 Low No red flag found
Higher than Industry Revenue GrowthA higher-than-industry revenue growth represents increased potential for the company to increase their market shareOver the last 5 years, revenue has grown at a yearly rate of 13.23%, vs industry avg of 7.66%Increasing Market ShareMarket share is the percentage of an industry's total sales going to a particular company. It gives a general idea of the size of a company v/s its competitorsOver the last 5 years, market share increased from 3% to 3.61%Higher than Industry Net IncomeNet income is equal to net earnings (profit) less expenses. This number is an important measure of how profitable the company isOver the last 5 years, net income has grown at a yearly r

...

https://www.tickertape.in/stocks/chemplast-sanmar-CHEMP?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
CHEMPLASTS
Chemplast Sanmar Ltd
49.56
https://www.tickertape.in/stocks/chemplast-sanmar-CHEMP/financials?checklist=basic&statement=income&view=normal&period=annual
Success : Requested ticker tape page is loaded successfully 
 Low Hasn't faired well - amongst the low performers
 High Seems to be overvalued vs the market average
 Avg Financials growth has been moderate for a few years
 High Showing good signs of profitability & efficiency
 Avg The stock is overpriced but is not in the overbought zone
 Low No red flag found
Lower than Industry Revenue GrowthA higher-than-industry revenue growth represents increased potential for the company to increase their market shareOver the last 5 years, revenue has grown at a yearly rate of 15.2%, vs industry avg of 16.1%Decreasing Market ShareMarket share is the percentage of an industry's total sales go

 Low Hasn't faired well - amongst the low performers
 High Seems to be overvalued vs the market average
 Low Lagging behind the market in financials growth
 Avg Average profitability - not good, not bad
 Avg The stock is not in the overbought zone
 Low No red flag found
Higher than Industry Revenue GrowthA higher-than-industry revenue growth represents increased potential for the company to increase their market shareOver the last 5 years, revenue has grown at a yearly rate of 63.48%, vs industry avg of 35.14%Increasing Market ShareMarket share is the percentage of an industry's total sales going to a particular company. It gives a general idea of the size of a company v/s its competitorsOver the last 5 years, market share increased from 1.98% to 5.04%
528.81
855.57
957.41
1,550.28
-299.43
-235.49
-88.88
-776.79
-346.81
-304.03
-150.25
-832.91
-337.43
-294.84
-141.92
-833.39
-------------------------------------------------
476
https://www.tickertape.in/stocks/sapphire-foods-india-SAPP

https://www.tickertape.in/stocks/metro-brands-METR?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
METROBRAND
Metro Brands Ltd
72.13
https://www.tickertape.in/stocks/metro-brands-METR/financials?checklist=basic&statement=income&view=normal&period=annual
Success : Requested ticker tape page is loaded successfully 
 Low Hasn't faired well - amongst the low performers
 High Seems to be overvalued vs the market average
 Avg Financials growth has been moderate for a few years
 High Showing good signs of profitability & efficiency
 Avg The stock is overpriced but is not in the overbought zone
 Low No red flag found
Higher than Industry Revenue GrowthA higher-than-industry revenue growth represents increased potential for the company to increase their market shareOver the last 5 years, revenue has grown at a yearly rate of 6.17%, vs industry avg of 4.56%Increasing Market ShareMarket share is the percentage of an industry's total sales going to a part

https://www.tickertape.in/stocks/rainbow-childrens-medicare-RAINB/financials?checklist=basic&statement=income&view=normal&period=annual
Success : Requested ticker tape page is loaded successfully 
 Low Hasn't faired well - amongst the low performers
 High Seems to be overvalued vs the market average
 Avg Financials growth has been moderate for a few years
 High Showing good signs of profitability & efficiency
 Avg The stock is overpriced but is not in the overbought zone
 Low No red flag found
Higher than Industry Revenue GrowthA higher-than-industry revenue growth represents increased potential for the company to increase their market shareOver the last 5 years, revenue has grown at a yearly rate of 24.46%, vs industry avg of 12.6%Increasing Market ShareMarket share is the percentage of an industry's total sales going to a particular company. It gives a general idea of the size of a company v/s its competitorsOver the last 5 years, market share increased from 1.17% to 1.82%Higher than

ACI
Archean Chemical Industries Ltd
18.76
https://www.tickertape.in/stocks/archean-chemical-industries-ACA/financials?checklist=basic&statement=income&view=normal&period=annual
Success : Requested ticker tape page is loaded successfully 
 Low Hasn't faired well - amongst the low performers
 High Seems to be overvalued vs the market average
 Low Lagging behind the market in financials growth
 High Showing good signs of profitability & efficiency
 Good The stock is underpriced and is not in the overbought zone
 Low No red flag found
Income statement not found
NAN
NAN
NAN
1,142.83
NAN
NAN
NAN
479.55
NAN
NAN
NAN
188.22
NAN
NAN
NAN
251.02
-------------------------------------------------
498
https://www.tickertape.in/stocks/five-star-business-finance-FIVES?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
FIVESTAR
Five-Star Business Finance Ltd
28.65
https://www.tickertape.in/stocks/five-star-business-finance-FIVES/financials?checklist=basic&statemen

## Create a file which contains CompanyNames with the base URL

In [8]:
#Now we will extract all the information which we require and we will put all the information extracted in an tsv format file
header_agent = {'User-Agent': 'Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.11 (KHTML, like Gecko) Chrome/23.0.1271.64 Safari/537.11',
       'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8',
       'Accept-Charset': 'ISO-8859-1,utf-8;q=0.7,*;q=0.3',
       'Accept-Encoding': 'none',
       'Accept-Language': 'en-US,en;q=0.8',
       'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8',
       'Connection': 'keep-alive'}
with open('companyListURL.tsv','w',newline='',encoding="utf-8") as file:
    headers = ['sNo','Company Name','URL']

    writer = csv.writer(file,delimiter='\t')
    writer.writerow(headers)
    SNo = 0
    for url_val in company_url:
        url_val_overview=url_val + "?checklist=basic&chartScope=1d"
        SNo=SNo+1
        print(SNo)
        company_ovr_page = requests.get(url_val_overview,headers=header_agent,stream=True)
        print(url_val_overview)
        if company_ovr_page.status_code == 200:
            print("Success : Requested ticker tape page is loaded successfully ")
            company_ovr_content = company_ovr_page.content
            comp_ovr_soup = BeautifulSoup(company_ovr_content,"html.parser")
            part_1 = comp_ovr_soup.find('div', attrs ={'class':'jsx-3488654145 sidebar desktop--only stock-security-sidebar'})
            CompanyName = part_1.find('span', attrs ={'class':'jsx-3488654145 ticker text-teritiary font-medium'}).get_text()
            print(CompanyName)
            row = [SNo,CompanyName,url_val]
            writer.writerow(row)
            
            print("-------------------------------------------------")

1
https://www.tickertape.in/stocks/aditya-birla-fashion-and-retail-ADIA?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
ABFRL
-------------------------------------------------
2
https://www.tickertape.in/stocks/affle-india-AFFL?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
AFFLE
-------------------------------------------------
3
https://www.tickertape.in/stocks/aarti-drugs-ADRG?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
AARTIDRUGS
-------------------------------------------------
4
https://www.tickertape.in/stocks/aarti-industries-ARTI?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
AARTIIND
-------------------------------------------------
5
https://www.tickertape.in/stocks/acc-ACC?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
ACC
---------------------------------

BDL
-------------------------------------------------
41
https://www.tickertape.in/stocks/bharat-forge-BFRG?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
BHARATFORG
-------------------------------------------------
42
https://www.tickertape.in/stocks/bajaj-finserv-BJFS?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
BAJAJFINSV
-------------------------------------------------
43
https://www.tickertape.in/stocks/berger-paints-india-BRGR?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
BERGEPAINT
-------------------------------------------------
44
https://www.tickertape.in/stocks/bata-india-BATA?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
BATAINDIA
-------------------------------------------------
45
https://www.tickertape.in/stocks/bajaj-auto-BAJA?checklist=basic&chartScope=1d
Success : Requested ticker tape pag

https://www.tickertape.in/stocks/chalet-hotels-CHAL?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
CHALET
-------------------------------------------------
82
https://www.tickertape.in/stocks/carborundum-universal-CRBR?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
CARBORUNIV
-------------------------------------------------
83
https://www.tickertape.in/stocks/ceat-CEAT?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
CEATLTD
-------------------------------------------------
84
https://www.tickertape.in/stocks/cesc-CESC?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
CESC
-------------------------------------------------
85
https://www.tickertape.in/stocks/cipla-CIPL?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
CIPLA
-------------------------------------------------
86
h

https://www.tickertape.in/stocks/emami-EMAM?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
EMAMILTD
-------------------------------------------------
122
https://www.tickertape.in/stocks/divis-laboratories-DIVI?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
DIVISLAB
-------------------------------------------------
123
https://www.tickertape.in/stocks/eicher-motors-EICH?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
EICHERMOT
-------------------------------------------------
124
https://www.tickertape.in/stocks/gujarat-fluorochemicals-GUJL?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
FLUOROCHEM
-------------------------------------------------
125
https://www.tickertape.in/stocks/engineers-india-ENGI?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
ENGINERSIN
----------

https://www.tickertape.in/stocks/gujarat-state-petronet-GSPT?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
GSPL
-------------------------------------------------
161
https://www.tickertape.in/stocks/gujarat-gas-GGAS?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
GUJGASLTD
-------------------------------------------------
162
https://www.tickertape.in/stocks/havells-india-HVEL?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
HAVELLS
-------------------------------------------------
163
https://www.tickertape.in/stocks/gujarat-alkalies-and-chemicals-GALK?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
GUJALKALI
-------------------------------------------------
164
https://www.tickertape.in/stocks/grasim-industries-GRAS?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
GRASIM
-

...

PIIND
-------------------------------------------------
319
https://www.tickertape.in/stocks/pfizer-PFIZ?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
PFIZER
-------------------------------------------------
320
https://www.tickertape.in/stocks/pnb-housing-finance-PNBH?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
PNBHOUSING
-------------------------------------------------
321
https://www.tickertape.in/stocks/prestige-estates-projects-PREG?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
PRESTIGE
-------------------------------------------------
322
https://www.tickertape.in/stocks/prince-pipes-and-fittings-PRCE?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
PRINCEPIPE
-------------------------------------------------
323
https://www.tickertape.in/stocks/power-grid-corporation-of-india-PGRD?checklist=basic&chart

https://www.tickertape.in/stocks/shoppers-stop-SHOP?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
SHOPERSTOP
-------------------------------------------------
359
https://www.tickertape.in/stocks/sharda-cropchem-SHCR?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
SHARDACROP
-------------------------------------------------
360
https://www.tickertape.in/stocks/shree-cement-SHCM?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
SHREECEM
-------------------------------------------------
361
https://www.tickertape.in/stocks/sbi-life-insurance-company-SBIL?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
SBILIFE
-------------------------------------------------
362
https://www.tickertape.in/stocks/solar-industries-india-SLIN?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
SOLARIN

SWANENERGY
-------------------------------------------------
398
https://www.tickertape.in/stocks/tata-consultancy-services-TCS?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
TCS
-------------------------------------------------
399
https://www.tickertape.in/stocks/tata-investment-corporation-TINV?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
TATAINVEST
-------------------------------------------------
400
https://www.tickertape.in/stocks/teamlease-services-TLSV?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
TEAMLEASE
-------------------------------------------------
401
https://www.tickertape.in/stocks/tech-mahindra-TEML?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
TECHM
-------------------------------------------------
402
https://www.tickertape.in/stocks/titan-company-TITN?checklist=basic&chartScope=1d
Succ

https://www.tickertape.in/stocks/zydus-wellness-ZYDS?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
ZYDUSWELL
-------------------------------------------------
439
https://www.tickertape.in/stocks/zee-entertainment-enterprises-ZEE?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
ZEEL
-------------------------------------------------
440
https://www.tickertape.in/stocks/zensar-technologies-ZENT?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
ZENSARTECH
-------------------------------------------------
441
https://www.tickertape.in/stocks/yes-bank-YESB?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
YESBANK
-------------------------------------------------
442
https://www.tickertape.in/stocks/hle-glascoat-HLE?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
HLEGLAS
------------

SAPPHIRE
-------------------------------------------------
477
https://www.tickertape.in/stocks/one-97-communications-PAY?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
PAYTM
-------------------------------------------------
478
https://www.tickertape.in/stocks/latent-view-analytics-LATE?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
LATENTVIEW
-------------------------------------------------
479
https://www.tickertape.in/stocks/go-fashion-india-GOC?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
GOCOLORS
-------------------------------------------------
480
https://www.tickertape.in/stocks/star-health-and-allied-insurance-company-STARH?checklist=basic&chartScope=1d
Success : Requested ticker tape page is loaded successfully 
STARHEALTH
-------------------------------------------------
481
https://www.tickertape.in/stocks/ce-info-systems-MAPM?checklist=bas

### Creating A file after Web scrapping news data from Ticker Tape website

In [10]:

    
with open('companyNewsList.tsv','w',newline='',encoding="utf-8") as file:
    headers = ['sNo','Company Name','Full Company Name','News Title','News Article','News Summary','NewsDate']

    writer = csv.writer(file,delimiter='\t')
    writer.writerow(headers)
    SNo = 0
    for url_val in company_url:
        url_val_news=url_val + "/news?checklist=basic&type=news"
        SNo=SNo+1
        
        company_news_page = requests.get(url_val_news)
        print(url_val_news)
        if company_news_page.status_code == 200:
            print("Success : Requested ticker tape page is loaded successfully ")
            company_news_content = company_news_page.content
            comp_news_soup = BeautifulSoup(company_news_content,"html.parser")
            leftsidebar = comp_news_soup.find('div', attrs ={'class':'desktop-side-panel desktop--only'})
            CompanyName = leftsidebar.find('span', attrs ={'class':'jsx-3488654145 ticker text-teritiary font-medium'}).get_text()
            FullCompanyName = leftsidebar.find('div', attrs ={'class':'jsx-3488654145 full-width d-flex justify-space-between sidebar-security-name'}).get_text()

            news_section = comp_news_soup.find('div', attrs ={'class':'jsx-4278471340'})
#             print(news_section)
            news_cards = news_section.select('.latest-news-holder a')

            for card in news_cards:
                NewsURL = card['href']
                NewsTitle = card.select_one('.news-title').text.strip()
                jsx_value = card['class'][1]  # Assuming the `jsx-3953764037` class is always the second class
                NewsDate = card.select_one('.news-info span').text.strip()
                print("Full Company Name:",FullCompanyName)
                print("Company Name:",CompanyName)
                print("News URL:", NewsURL)
                print("News Title:", NewsTitle)
                print("News Date:", NewsDate)
                news_article = Article(NewsURL) #providing the link
                try:
                  news_article.download()
                  news_article.parse()
                  news_article.nlp()
                except:
                   pass 
                NewsArticle=news_article.text
                NewsSummary=news_article.summary
                print("News Article:",NewsArticle)
                print("News Summary:", NewsSummary)
                
                row = [SNo,CompanyName,FullCompanyName,NewsTitle,NewsArticle,NewsSummary,NewsDate]
                writer.writerow(row)
#             
                
        print("-----------------------------")        

https://www.tickertape.in/stocks/aditya-birla-fashion-and-retail-ADIA/news?checklist=basic&type=news
Success : Requested ticker tape page is loaded successfully 
-----------------------------
https://www.tickertape.in/stocks/affle-india-AFFL/news?checklist=basic&type=news
Success : Requested ticker tape page is loaded successfully 
-----------------------------
https://www.tickertape.in/stocks/aarti-drugs-ADRG/news?checklist=basic&type=news
Success : Requested ticker tape page is loaded successfully 
-----------------------------
https://www.tickertape.in/stocks/aarti-industries-ARTI/news?checklist=basic&type=news
Success : Requested ticker tape page is loaded successfully 
Full Company Name: Aarti Industries Ltd
Company Name: AARTIIND
News URL: https://www.moneycontrol.com/news/business/markets/trade-setup-for-wednesday-top-15-things-to-know-before-the-opening-bell-39-10754031.html
News Title: Trade setup for Wednesday: Top 15 things to know before the opening bell
News Date: 5 days a

https://www.tickertape.in/stocks/acc-ACC/news?checklist=basic&type=news
Success : Requested ticker tape page is loaded successfully 
Full Company Name: ACC Ltd
Company Name: ACC
News URL: https://zeenews.india.com/india/who-is-nitin-agarwal-new-dg-of-bsf-and-kerala-cadre-ips-officer-check-his-salary-under-7th-pay-commission-perks-2620496.html
News Title: Who Is Nitin Agarwal, New DG Of BSF And Kerala Cadre IPS Officer? Check His Salary Under 7th Pay Commission, Perks
News Date: 12 hours ago
News Article: After lying vacant for five months post the retirement of Pankaj Kumar Singh in December 2022, the country's prestigious Border Security Force (BSF) got its new chief on Sunday. The development came after a late-night order by the Appointments Committee of the Cabinet (ACC) approved the Ministry Of Home Affairs proposal of appointing Nitin Agarwal as the new Director General of the BSF. The Border Security Force is the country's premier security agency primarily tasked to guard the 4,0

https://www.tickertape.in/stocks/adani-green-energy-ADNA/news?checklist=basic&type=news
Success : Requested ticker tape page is loaded successfully 
Full Company Name: Adani Green Energy Ltd
Company Name: ADANIGREEN
News URL: https://www.thehindubusinessline.com/markets/nse-revises-price-bands-on-three-adani-group-companies/article66940525.ece
News Title: NSE revises price bands on three Adani Group companies
News Date: 5 days ago
News Article: National Stock Exchange (NSE) has revised price bands on three Adani Group companies, effective June 7, according to its website.

The price band on Adani Transmission Ltd was revised from 5 per cent to 10 per cent, Adani Power Ltd from 5 per cent to 20 per cent and Adani Green Energy Ltd from 5 per cent to 10 per cent.
News Summary: National Stock Exchange (NSE) has revised price bands on three Adani Group companies, effective June 7, according to its website.
The price band on Adani Transmission Ltd was revised from 5 per cent to 10 per cent, 

News Article: Shares of four Adani group companies are in focus on Wednesday morning following upward revision in their circuit limits by stock exchanges. In the case of Adani Power, the circuit limit has been revised to 20 per cent from 5 per cent earlier. For Adani Green Energy, Adani Wilmar and Adani Transmission, the circuit limit has been changed to 10 per cent from 5 per cent earlier. The move came a week after NSE and BSE removed the securities of Adani Enterprises from the short-term ASM framework. On May 24, both the bourses put Adani Enterprises under the short-term additional surveillance measure (ASM) framework.

The Gautam Adani-led group, which has interests ranging from ports to airports, from electricity generation to transmission and distribution, from edible oil to FMCG products, logistics, cement, and roads, recorded its highest ever Ebitda at group portfolio level of Rs 57,219 crore in FY23, up 36 per cent YoY.

Adani portfolio companies operate in utility and infra

News Article: Shares of three Adani group companies namely Adani Green Energy, Adani Transmission and Adani Ports & SEZ are in focus on Thursday morning after a media report quoting sources suggested that the group may revisit global bond markets by September to raise up to $2 billion via sustainability-linked and green bonds.

In May, a Bloomberg report suggested that Adani Green Energy, Adani Transmission and Adani Enterprises could raise between $3 billion and $5 billion, citing people familiar with the matter. Abu Dhabi-based International Holding Co, which invested almost $2 billion in Adani companies, did not plan to take part in any potential share or bond sales, IHC's spokesperson Ahmed Ibrahim had told Reuters in May.

Adani group has been in news of late as the group announced completion of its prepayment programme, aggregating $2.65 billion. The group had went on deleveraging drive in an attempt to win back investor trust post a scathing report by the US short seller Hindenb

...

News Article: Representative Image

Shares of new-age fintech companies, Paytm operator One97 Communications and PB Fintech were in focus on June 8 after global research and broking firm Bank of America Securities changed its ratings for the two stocks.

BoFA upgraded its rating for One97 Communications to 'buy' while also raising its price target for the stock by nearly 10 percent to Rs 855. The broking firm cited expectations of a strong revenue momentum for the company as the reason behind the upgrade.

The brokerage holds the view that Paytm possesses significant potential for positive operational leverage and sits in a 'sweet-spot' due to limited competition. Additionally, BoFA also highlighted other positive factors such as the growth of digitalization driving payments and the company's robust cash balance.

Shares of One97 Communications also reacted positively to the ratings upgrade and at 12.21 pm, were trading at Rs 769.50 on the NSE, up 5.85 percent from the previous close. 

News Article: Representative Image

live bse live

nse live Volume Todays L/H More ×

Shares of One97 Communications, the operator of Paytm, gained over 3 percent on June 9, a day after the Reserve Bank of India (RBI) approved the First Loss Default Guarantee (FLDG) programme.

The FLDG is a popular product that fintechs in the country use to form partnerships with banks and non-banking financial companies (NBFCs). It helps banks and NBFCs cover potential losses, as well as gives them confidence that fintechs understand credit risk. Under FLDG, fintechs help banks and NBFCs recoup losses that occur when customers default on payments.

At 2.45 pm, the stock was quoting at Rs 801.90 on the NSE, higher by 3.8 percent from the previous close. The stock has been on a three-day gaining streak and is up over 12 percent.

Follow our live blog for all the market action

Before the digital lending norms were introduced, fintechs and banks had developed an FLDG model on their own where the former

News Article: Shares of Go Fashion Ltd. fell as much as 5.13% before erasing some losses to trade 4.10 lower at 10 a.m., compared to a 0.12% gain in the benchmark NSE Nifty 50. The total traded volume so far in the day stood at 1,900 times its 30-day average.

The Chennai-based company was the worst performer among Nifty 500 peers at the time.

All seven analysts tracking the company maintain a 'buy', according to Bloomberg data. The average of 12-month price targets suggests an upside of 16.6%.
News Summary: Shares of Go Fashion Ltd. fell as much as 5.13% before erasing some losses to trade 4.10 lower at 10 a.m., compared to a 0.12% gain in the benchmark NSE Nifty 50.
The total traded volume so far in the day stood at 1,900 times its 30-day average.
The Chennai-based company was the worst performer among Nifty 500 peers at the time.
All seven analysts tracking the company maintain a 'buy', according to Bloomberg data.
The average of 12-month price targets suggests an upside of 16.6%.


News Article: The founder of one of the largest private sector health insurers Star Health and Allied Insurance Company Ltd Venkatasamy Jagannathan has tendered his resignation from its Board with immediate effect, industry sources said on Sunday.

An industry veteran, Jagannathan had stepped down from his role as the Chairman of the city-headquartered firm in May.

"...we wish to inform you that Venkatasamy Jagannathan vide e-mail dated June 10, 2023 has tendered his resignation from the Board of the Company with immediate effect from June 10, 2023," Star Health and Allied Insurance Company Ltd said in a BSE filing on Saturday.

Jagannathan, after attaining superannuation from the United India Insurance as its Chairman and Managing Director, founded Star Health and Allied Insurance with the backing of Dubai-based ETA Group.

"We started with just 12 people, rented premises with Rs 30,000. Star Health is now valued at more than Rs 30,000 crore," he said.

According to company's FY 2021

News Article: The National Company Law Tribunal NCLT ) Thursday accepted Delhivery 's notice seeking declaration of Go First 's voluntary insolvency resolution as "fraudulent and malicious." It gave the interim resolution professional (IRP) of the Wadia-group airline two weeks to reply."Go First received ₹57 lakh on May 2 from Delhivery as advance for future services, knowing fully well they were filing for insolvency," said the counsel for Delhivery. Under Section 65 of the Insolvency and Bankruptcy Code (IBC), 2016, fraudulent and malicious initiation of insolvency proceedings can invite a penalty of ₹1 lakh to ₹1 crore.Counsel for the IRP asked the court to also implead the former management but the bench directed the resolution professional to file a reply in the matter and listed it for July 24. Delhivery will have a week to submit a rejoinder, after the filing of the carrier's reply.Go First, in its voluntary insolvency resolution application filed under Section 10 of the IBC, ha